In [1]:
import pandas as pd
from prettytable import PrettyTable
from ydata_profiling import ProfileReport

In [2]:
original = pd.read_excel('./original.xlsx')

In [3]:
ProfileReport(original)

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

<div style="background-color: rgba(150, 0,50, .5); border-radius: 20px; padding: 20px; color: white" >

<ul>
    <li>
        this report shows that three columns are of unsupported type: 'StockCode', 'InvoiceNo' and 'Description', which is a result of the fact that these columns contain data of different datatypes
    </li>
    </br>
    <li>
        the 'InvoiceNo' is not needed, so it will be deleted, the other two columns will be converted into String datatype
    </li></br>
    <li>
        before converting datatypes, a look into missing values tells us that the Description column has 0.3% missing data, if the description of the product is missing, the row will not provide any value for the study, therefore we'll delete it
    </li></br>
    <li>
        another problem we see is that the CustomerId field has a lot of missing values, to address this we'll split the logic into two loops, one to extract items from the subset with known CustomerID, and another to extract from the subset with missing CustomerID
    </li></br>
    <li>
        rows with missing CustomerId should not be deleted because it only signifies that a client bought something without being registered to the store system, the list of bought items is still important
    </li></br>
    <li>
        negative quantity values signifies returned items, which are not a subject for this study, therefore they'll be removed
    </li>
</ul>






</div>



# removing rows with missing Description

In [4]:
original.dropna(subset=['Description'], inplace=True)

# converting SotckCode and Description into String

In [5]:
original["StockCode"] = original["StockCode"].apply(lambda x: str(x))
original["Description"] = original["Description"].apply(lambda x: str(x))

# Removing negative quantities

In [6]:
original["Quantity"] = original[original["Quantity"] > 0]["Quantity"]

In [8]:
ProfileReport(original)

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

In [9]:
original_ = original.drop(columns=['InvoiceNo', 'Quantity', 'UnitPrice'])

# need to get what every Customer bought => unique by CustomerID
# but a customer can buy a lot of items at the time, different rows with same CustomerID represent one trasaction
# unique by time such that all transactions made in the range of X minutes will be considered as one transaction

In [18]:
# the time interval for transaction grouping in minutes
time_interval = 15

transactions = []

# extract list of transactions made by anonymous customers

In [11]:
reference_time = None
transaction = []
for _, customer_ in original_[original_["CustomerID"].isna()].iterrows():

    time = str(customer_['InvoiceDate']).split(' ')[1]
    hour = int(time[:2])
    minute = int(time[3:5])

    if reference_time is None:
        reference_time = {"h": hour, "m": minute}

    if hour == reference_time['h'] and abs(minute - reference_time['m']) <= time_interval:
        transaction.append(customer_['StockCode'])
    else:
        transactions.append(transaction)
        transaction = [customer_['StockCode']]
        reference_time = {"h": hour, "m": minute}

    transactions.append(transaction)
    



# extract the transactions list made by registered customers

In [25]:

for _, customer_ in original_.groupby('CustomerID'):
    print(customer_)
    break
    transaction = []
    reference_time = None

    for index, row in customer_.iterrows():
        time = str(row['InvoiceDate']).split(' ')[1]
        hour = int(time[:2])
        minute = int(time[3:5])

        if reference_time is None:
            reference_time = {"h": hour, "m": minute}

        if hour == reference_time['h'] and abs(minute - reference_time['m']) <= time_interval:
            transaction.append(row['StockCode'])
        else:
            transactions.append(transaction)
            transaction = [row['StockCode']]
            reference_time = {"h": hour, "m": minute}

    transactions.append(transaction)
    

      StockCode                     Description         InvoiceDate  \
61619     23166  MEDIUM CERAMIC TOP STORAGE JAR 2011-01-18 10:01:00   
61624     23166  MEDIUM CERAMIC TOP STORAGE JAR 2011-01-18 10:17:00   

       CustomerID         Country  
61619     12346.0  United Kingdom  
61624     12346.0  United Kingdom  


In [20]:
len(transactions)

19314

In [21]:
apriory_df = pd.DataFrame(transactions)


In [22]:
apriory_df.shape

(19314, 543)

In [16]:
apriory_df.to_excel('./transactions.xlsx', index=False)


KeyboardInterrupt



<div style="background-color: rgba(0, 255,50, .5); border-radius: 20px; padding: 20px; color: white" >
    because we used the StockCode of items, we will need to map each StockCode to its corresponding item 
</div>



In [ ]:
mapping = []
for code, row in original_.groupby('StockCode'):
    mapping.append([code, row["Description"].iloc[0]])

In [ ]:
table = PrettyTable(['Code', 'Product'])
for row in mapping:
    table.add_row(row)

print(table)

+--------------+-------------------------------------+
|     Code     |               Product               |
+--------------+-------------------------------------+
|    10002     |     INFLATABLE POLITICAL GLOBE      |
|    10080     |       GROOVY CACTUS INFLATABLE      |
|    10120     |             DOGGY RUBBER            |
|    10125     |       MINI FUNKY DESIGN TAPES       |
|    10133     |     COLOURING PENCILS BROWN TUBE    |
|    10134     |                 nan                 |
|    10135     |     COLOURING PENCILS BROWN TUBE    |
|    11001     |     ASSTD DESIGN RACING CAR PEN     |
|    15030     |           FAN BLACK FRAME           |
|    15034     |     PAPER POCKET TRAVELING FAN      |
|    15036     |      ASSORTED COLOURS SILK FAN      |
|    15039     |            SANDALWOOD FAN           |
|    16008     | SMALL FOLDING SCISSOR(POINTED EDGE) |
|    16010     |  FOLDING CAMPING SCISSOR W/KNIF & S |
|    16011     |           ANIMAL STICKERS           |
|    16012

In [ ]:
import sqlite3

# Load the Excel file into a Pandas DataFrame

# Create an in-memory SQLite database and insert the DataFrame into a table
conn = sqlite3.connect(':memory:')
original.to_sql('my_table', conn, index=False)

541909

In [ ]:


# Execute SQL queries on the DataFrame
query1 = 'SELECT StockCode, sum(Quantity) FROM my_table  group by (StockCode)'
result1 = pd.read_sql_query(query1, conn)
print(f"Result of Query 1:\n{result1}\n")


# Close the database connection
conn.close()

Result of Query 1:
         StockCode  sum(Quantity)
0            10002           1037
1            10080            495
2            10120            193
3           10123C            -13
4           10123G            -38
...            ...            ...
4065  gift_0001_20             20
4066  gift_0001_30             37
4067  gift_0001_40              3
4068  gift_0001_50              4
4069             m              1

[4070 rows x 2 columns]



In [ ]:
sum = 0
for index, row in original.iterrows():
    if row["StockCode"] == "10123C" : 
        print(f"found at {index} with quality: {row['Quantity']}")
        sum += row["Quantity"]
    
print(sum)

    

found at 5451 with quality: 1
found at 109611 with quality: 3
found at 140929 with quality: 1
found at 265293 with quality: -18
-13
